# 7CUSMSDA_Week4_Point Pattern Analysis (PPA) 
<a href="#This Week's Overview">This Week's Overview</a>

<a href="#Learning Outcomes">Learning Outcomes</a>

<a href="#Get prepared">Get prepared</a>
- <a href="#What is Point Pattern Analysis (PPA)">What is Point Pattern Analysis (PPA)</a>

<a href="#CSR vs. Real points">CSR vs. Real points</a>
- <a href="#Convex hull">Convex hull</a>
- <a href="#Shape analysis">Shape analysis</a>
- <a href="#Centrography analysis">Centrography analysis</a>
- <a href="#Dispersion measures">Dispersion measures</a>

<a href="#Density Estimates">Density Estimates</a>
- <a href="#Quadrat Based Statistics">Quadrat Based Statistics</a>
- <a href="#Window attributes & methods">Window attributes & methods</a>
- <a href="#Point Intensity Estimates">Point Intensity Estimates</a>
 
<a href="#Heatmap of London Pubs">Heatmap of London Pubs</a>

<a href="#Finding Nearest Neighbors">Finding Nearest Neighbors</a>
- <a href="#Nearest Neighbors">Nearest Neighbors</a>
- <a href="#Mean Nearest Neighbor Distance Statistics">Mean Nearest Neighbor Distance Statistics</a>
- <a href="#Nearest Neighbor Distance Functions">Nearest Neighbor Distance Functions</a>
- <a href="#K Nearest Neighbors (KNN)">K Nearest Neighbors (KNN)</a>
  - <a href="#k-nearest neighbor weights">k-nearest neighbor weights</a>
  - <a href="#Distance band weights">Distance band weights</a>
  - <a href="#Kernel weights">Kernel weights</a>

<a href="#Nearest Neighbors Classification Visualization">Nearest Neighbors Classification Visualization<a/>
- <a href="#Finding Nearest Neighbors">Finding Nearest Neighbors</a> 
- <a href="#Classification Accuracy">Classification Accuracy</a>


<a href="#Kernel Density Estimation (KDE)">Kernel Density Estimation (KDE)</a>
- <a href="#Univariate Distribution in 1D">Univariate Distribution in 1D</a>
- <a href="#Bivariate Distribution in 2D">Bivariate Distribution in 2D</a> 
- <a href="#Others channels to understand KDE">Others channels to understand KDE</a> 
- <a href="#Multivariate KDE">Multivariate KDE<a/> 




- <a href="#Task 1">Task 1</a>
- <a href="#Task 2">Task 2</a>
- <a href="#Task 3">Task 3</a>
- <a href="#Task 4">Task 4</a>
- <a href="#Task 5">Task 5</a>
- <a href="#Task 6">Task 6</a>
- <a href="#Task 7">Task 7</a> (Optional)
- <a href="#Task 8">Task 8</a>
- <a href="#Task 9">Task 9</a>
- <a href="#Task 10">Task 10</a>

## <a id="This Week's Overview">This Week's Overview</a>

This week, we will use point datasets (both randomly generated CSR data and London pubs data) to develop our capability in using `pointpats` from `PySAL` on spatial point pattern analysis, visualization and exploration. Tasks for this week will mainly focus on visualizing spatial point patterns, exploring *distance-based* and *density-based* spatial point patterns analysis on:

- Point processing.
- Point distribution analysis (i.e.Centrography and visualization). 
- *Distance-based methods* are commonly used for interpreting the second order effects – where and what kind of clusters are formed; thus suitable for identifying local patterns.
- *Density-based methods*, they are often used for understanding the first order effects – how many and how often points can be found, and where their spatial mean is; thus good at capturing the global tendency.

## <a id="Learning Outcomes">Learning Outcomes</a> 
Upon the completion of this practical, you will get comparative understanding on distance-based and density-based methods for point pattern analysis, especially the following:

By the end of this practical you should be able to:
- explore the nature of points distribution
- measure the centrality and the spatial dispersion of points
- familiarise ourselves with distance based point pattern analysis methods
- practice on quadrat based statistics and point density estimates
- know how to realize density based visualization by interactive heatmap 
- get knowledge on machine learning using Nearest Neighbours Classification
- recap on Kernel Density Estimates (KDE)

New libraries such as `Bokeh` and `statsmodels` will be introduced in this practical as well.

## <a id="Get prepared">Get prepared</a>
- Set up a **"data"** folder in your directory for this notebook
- <font color="red">Copy the data </font> we've used for previous weeks (LSOA_IMD2019 shapefile, Airbnb listings data) into the "**"data"**" folder.

More details on the metadata of IMD2019 (English Indices of Deprivation 2019) could be found [here](https://opendatacommunities.org/resource?uri=http%3A%2F%2Fopendatacommunities.org%2Fdata%2Fsocietal-wellbeing%2Fimd2019%2Findices).

We will import the general libraries at this stage, but import other specific libraries by section to help you better understand their functions. 

In [1]:
import os
import urllib
import zipfile
import re

import numpy as np
import pandas as pd
import geopandas as gpd
import pysal as ps
import libpysal as lps
import matplotlib.pyplot as plt
import matplotlib.collections as mplc
%matplotlib inline
import seaborn as sns
import shapely

from shapely import geometry as sgeom
from shapely.geometry import Point
import descartes as des
import pointpats 
from pointpats import PointPattern
from shapely import ops
from pointpats import PoissonPointProcess as ppp_csr
#from pysal.contrib.viz import mapping as maps # For maps.plot_choropleth

import warnings
warnings.simplefilter('ignore') 

### <a id="What is Point Pattern Analysis (PPA)">What is Point Pattern Analysis (PPA)</a>

What are points in space? Should we simply take them as locations of interest? We could normally categorize points into 2 groups as **Event Points** and **Arbitrary Points**. 
- *Event Points* are locations where something of interest has occurred, hence could represent [a wide variety of phenomena](https://en.wikipedia.org/wiki/Point_process). 
- *Arbitrary Points* are locations where the phenomena of interest has not been observed, such as the so-called "empty space" or "regular" points. 

As our practicals mostly looking at real life data in our society, so you will be given **Event Points** to observe their collective spatial pattern characteristics. Let's recall the concept of `complete spatial randomness (CSR)` introduced in lecture: if there are a series of *point locations*, $(p_1, p_2, \ldots, p_n)$ in a two-dimensional study region $\Re$, then for point location $i$, its spatial identity should be $p_i = (x_i, y_i)$. 

If it is a `CSR` process, then the points are independent from one another (generated from stochastic process, and with constant probability); 

If the point patterns are not under `CSR` (which is the normal case), they could be affected by **First order effects** and **Second order effects** covered in lecture. 
- *First order effects*: Non-CRS point process' intensity pattern driven by underlying covariate.
- *Second order effects*: Non-CRS point process due to interaction and dependence between events in space. 

So to further investigate the process' spatial structure, detect the points' deviations from `CSR` and test the point pattern statistics, we will use the main mathods from point pattern analysis module `pointpats` in `PySAL` as below:
1. Point Processing
2. Centrography and Visualization
3. Nearest Neighbors

## <a id="CSR vs. Real points">CSR vs. Real points</a>

Let's start with simulating a 1000-point dataset within London boundary from a `CSR (complete spatial randomness)` process. From your lecture, you may realize that `CSR` events follow a homogeneous Poisson Process over the study region $\Re$. Hence, point pattern is considered to be number of events occurring in sub-regions A, of the whole study region $\Re$.

<img src="Picture1.png" style="width: 100px;"/>

where Y(A) is the number of events occurring in the area A, following a Poisson distribution with mean λA.
<img src="Picture2.png" style="width: 200px;"/>

So given N events in A, they are (1) independent random sample from a uniform distribution with equal probability of occurring at any position, indicating no first order effects; (2) independent of the position of any other, implying no spatial interaction with one another.

In the following section, we will call `PoissonPointProcess` in `pointpats` to generate the dataset. It is similar with the previous practice on getting random point data: we generate events with x coordinates from a uniform distribution on $(x_1,x_2,...,x_i)$ and y coordinates from a uniform distribution on $(y_1,y_2,...,y_i)$. So a real-world observed pattern of points can be compared with the simulated ones based on CSR, in order to assess whether observed patterns are regular, clustered or random distribution.

For more references, you may find the `pointpats` documents at <https://pointpats.readthedocs.io/en/latest/index.html>



In [2]:
# import necessary libraries for this section
from pysal.lib.cg import shapely_ext
from pointpats import window
from pointpats.window import poly_from_bbox, as_window, Window, to_ccf
import pointpats.quadrat_statistics as qs

In [3]:
# open London lsoa polygon shapefile
lsoas = ps.lib.io.open ('data/LSOA_IMD2019.shp') 
# define the polygon shapes from London lsoa data
polys = [shp for shp in lsoas] 
# Create the exterior polygons for Greater London from the union of the polygon shapes
boundary = shapely_ext.cascaded_union(polys)

In [4]:
# generate 1000 points following csr process
# define its region boundary as london boundary
pp = ppp_csr(as_window(boundary), 1000, 1, asPP=True).realizations[0] 
# You may find realizations at index 0, which means first realized point pattern
# plot your point pattern out
pp.plot(window=True)

Here you may find a parameter **"window"**, and a function `as_window`, which play important roles in point pattern analysis. A window can define the domain for the point pattern, can support corrections for **edge effects**, and can also be used for point density analysis. In the following sections, we will use London pubs data as the basis for point pattern analysis.

Download the London Pubs shapefile data from CUSP github into your data folder, and get it ready for use. 

**Hint**: open point data from shapefile by calling `PointPattern` function, you need to pay attention to its array nature. This data will be used for following tasks, with coordinates for UTM zone 30U.

In [5]:
# Create the data dir if it doesn't exist
if os.path.isdir('data') is not True:
    print("Creating 'data' directory...")
    os.mkdir('data')

# Configure the download
url  = 'https://github.com/cusp-london/Spatial-Data-Analysis/blob/master/London_Pubs.zip?raw=true'
path = os.path.join("data","London_Pubs.zip")

# Download
r    = urllib.request.urlretrieve(url, path)

# Unzip it into the data folder
z    = zipfile.ZipFile(path)
m    = z.extractall("data")

In [6]:
pubs = gpd.read_file('data/London_Pubs/London_Pubs.shp')
pubs = pubs.to_crs({'init': 'epsg:27700'})
pubs.to_file('data/London_Pubs/London_Pubs_BNG.shp')

In [3]:
f = ps.lib.io.open('data/London_Pubs/London_Pubs_BNG.shp')
# get the points
pp_pubs = PointPattern(np.asarray([pnt for pnt in f]))
f.close() # why we need to call f.close()?
# # get the points plotted
pp_pubs.plot() 

In the following, we will use the 1000 CSR points as example to illustrate various spatial point pattern characteristics, and let you to complete corresponding tasks by using London pubs data.

### <a id="Convex Hull">Convex Hull</a>
The 1000 points following CSR process were now plotted within the London boundary, now let's try something different. Have you spotted any differences and why? What is `convex hull`?

In [87]:
pp.plot(window=True, hull=True) 

`Convex hull`  is the set of all convex combinations of the points. Does it look like an envelope? That's why it is also called `convex envelope` or `convex closure` in an affine space over the points.

### <a id="Task 1">Task 1</a>
Get the convex hull for London pubs data below, and compare the output with plot above.

In [88]:
# your code here
pp_pubs.plot(window=True, hull=True)

### <a id="Shape analysis">Shape analysis</a>

The full function of  `hull` is actually a measure for *shape analysis* of point pattern. So we are going to explore two methods: `Convex Hull (Hull)` and `Minimum Bounding Rectangle (mbr)`, as follows.

1. [Convex Hull](https://en.wikipedia.org/wiki/Convex_hull) is the smallest convex set that contains a point pattern *pp*, and could get realized through calling function **hull**.

2. [Minimum Bounding Rectangle (Box)](https://en.wikipedia.org/wiki/Minimum_bounding_rectangle) is the same as the minimum bounding Rectangle of its convex hull, which is bigger than convex hull, by calling **mbr** function to calculate the vertices' values.

In [89]:
# import relevant methods
from pointpats.centrography import hull, mbr
# get the points defining convex hull
hull(pp.points)

array([[504198.94627512, 176299.33647391],
       [516843.07538257, 160414.75063755],
       [531526.72069753, 156476.35205421],
       [540992.97392111, 158390.50960175],
       [544621.23527787, 159229.98574895],
       [547573.73309589, 161177.86530943],
       [560688.21199695, 185790.0353536 ],
       [556863.85306235, 190603.62322986],
       [554562.40729127, 193082.2963241 ],
       [535082.5336461 , 199949.30546872],
       [531958.93342399, 200567.35116713],
       [531698.38446224, 200517.73264145],
       [527289.77590523, 199390.55997382],
       [504304.17410645, 192777.5738365 ],
       [504279.71238246, 189805.05564042]])

In [16]:
# get the points defining minimum bounding rectangle
mbr(pp.points)

(504198.9462751194, 156476.35205420764, 560688.2119969521, 200567.35116712865)

In [ ]:
# Could you write the four vertices of the minimum bounding rectangle then?

(504198.9462751194, 156476.35205420764), (560688.2119969521, 156476.35205420764), (560688.2119969521, 200567.35116712865), (504198.9462751194, 200567.35116712865).

In [90]:
from matplotlib.patches import Rectangle
ax=pp.plot(get_ax=True, title ='Convex hull and MBR', hull=True)
mbr_pts=mbr(pp.points)
mbr_patch=Rectangle((mbr_pts[0], mbr_pts[1]), mbr_pts[2]-mbr_pts[0], mbr_pts[3]-mbr_pts[1], alpha=0.2)
ax.add_patch(mbr_patch)

### <a id="Centrography analysis">Centrography analysis</a>

Once we were given a point data set, normally we want to first detect where the center is. Hence the center point of two-dimensional point data distribution pattern could be termed as `Central Tendency`, and could be measured by calling these four listed functions in order. 
1. `mean_center`:  the mean center of the unmarked point pattern.
2. `weighted_mean_center`:  the weighted mean center of the marked point pattern.
3. `manhattan_median`:  the manhattan median
4. `euclidean_median`:  the Euclidean median

As they have their respective pros and cons, so for your own project data in the future, the appropriate measures should be selected carefully according to your specific objective and corresponding data description. But now let's just have a general view of all of them.

In [8]:
#import four centrography analysis functions 
from pointpats.centrography import mean_center, weighted_mean_center, manhattan_median, euclidean_median

In [10]:
# mean center calculation
mc = mean_center(pp.points)
# weighted mean center calculation
# define the weights
weights = np.arange(1000)
wmc = weighted_mean_center(pp.points, weights)
# Manhattan Median calculation
mm = manhattan_median(pp.points)
# Euclidean Median calculation
em = euclidean_median(pp.points)
pp.plot(window=True, hull=True)
plt.plot(mc[0], mc[1], 'r^', label='Mean Center')
plt.plot(wmc[0], wmc[1], 'gd', label='Weighted Mean Center')
plt.plot(mm[0], mm[1], 'yv', label='Manhattan Median') # "y" means yellow, "v" defines the icon's shape
plt.plot(em[0], em[1], 'm+', label='Euclidean Median')
plt.legend(numpoints=1)

For each method to calculate the mean/median center, think of the data format of coordinates, can you help yourself to list the coordinates information for these 4 points below?

**____________________________________________________________________**


In [15]:
h=pd.DataFrame({'name':['Mean Center','Weighted Mean Center', 'Manhattan Median', 'Euclidean Median'],
               'x':[mc[0],wmc[0],mm[0],em[0]],
               'y':[mc[1],wmc[1],mm[1],em[1]]})

geometry = [Point(xy) for xy in zip(h.x, h.y)]
hg = gpd.GeoDataFrame(h, geometry=geometry)
hg.crs = {'init' :'epsg:27700'}  
hg.to_crs({'init' :'epsg:4326'})

name              x              y  \
0           Mean Center  530825.843731  179509.779121   
1  Weighted Mean Center  530817.845117  179499.686796   
2      Manhattan Median  530440.108991  180666.950484   
3      Euclidean Median  530344.016958  179604.953511   

                    geometry  
0  POINT (-0.11664 51.49940)  
1  POINT (-0.11676 51.49931)  
2  POINT (-0.12177 51.50988)  
3  POINT (-0.12355 51.50036)

### <a id="Task 2">Task 2</a>
Use the London Pubs data to calculate its **mean center**, **weighted mean center**, **Manhattann median**, **Euclidean median** respectively, get the results plotted out in one figure; list their $(x,y)$ coordinates information as well.

In [17]:
# your code here for plot
mc_pubs = mean_center(pp_pubs.points)
weights_pubs=np.arange(len(pp_pubs.points))
wmc_pubs=weighted_mean_center(pp_pubs.points, weights_pubs)

# Manhattan Median calculation
mm_pubs = manhattan_median(pp_pubs.points)
# Euclidean Median calculation
em_pubs = euclidean_median(pp_pubs.points)

pp_pubs.plot(window=True, hull=True)
plt.plot(mc_pubs[0], mc_pubs[1], 'r^', label='Mean Center')
plt.plot(wmc_pubs[0], wmc_pubs[1], 'gd', label='Weighted Mean Center')
plt.plot(mm_pubs[0], mm_pubs[1], 'yv', label='Manhattan Median') # "y" means yellow, "v" defines the icon's shape
plt.plot(em_pubs[0], em_pubs[1], 'm+', label='Euclidean Median')
plt.legend(numpoints=1)

In [19]:
# your code here for printing point coordinates
h_pubs=pd.DataFrame({'name':['Mean Center','Weighted Mean Center', 'Manhattan Median', 'Euclidean Median'],
               'x':[mc_pubs[0],wmc_pubs[0],mm_pubs[0],em_pubs[0]],
               'y':[mc_pubs[1],wmc_pubs[1],mm_pubs[1],em_pubs[1]]})

geometry = [Point(xy) for xy in zip(h_pubs.x, h_pubs.y)]
hg_pubs = gpd.GeoDataFrame(h, geometry=geometry)
hg_pubs.crs = {'init' :'epsg:27700'}  
hg_pubs.to_crs({'init' :'epsg:4326'})

name              x              y  \
0           Mean Center  530825.843731  179509.779121   
1  Weighted Mean Center  530817.845117  179499.686796   
2      Manhattan Median  530440.108991  180666.950484   
3      Euclidean Median  530344.016958  179604.953511   

                    geometry  
0  POINT (-0.12953 51.50278)  
1  POINT (-0.12535 51.50252)  
2  POINT (-0.12223 51.51069)  
3  POINT (-0.12426 51.51067)

### <a id="Dispersion measures">Dispersion measures</a>

Standard distance is closely related to standard deviation of a dataset, and measures the dispersion of the events from their mean center $(x_m,y_m)$; hence a summary circle (standard distance circle) for the point pattern could be plotted based on the measurements, centered at $(x_m,y_m)$ with radius $SD$.

$$SD = \displaystyle \sqrt{\frac{\sum^n_{i=1}(x_i-x_{m})^2}{n} + \frac{\sum^n_{i=1}(y_i-y_{m})^2}{n}}$$

We will call the `std_distance` function to calculate the standard distance.

In [33]:
from pointpats.centrography import std_distance,ellipse

stdd = std_distance(pp.points)
circle1=plt.Circle((mc[0], mc[1]),stdd,color='g')
ax = pp.plot(get_ax=True, title='Standard Distance Circle', window=True)
ax.add_artist(circle1)
plt.plot(mc[0], mc[1], 'r^', label='Mean Center')
ax.set_aspect('equal')
plt.legend(numpoints=1)

### <a id="Task 3">Task 3</a>
Calculate the standard distance for London pubs and get the result plotted in yellow:

In [98]:
# your code here
stdd_pubs= std_distance(pp_pubs.points)
print ('standard distance: ', stdd_pubs)
circle2=plt.Circle((mc_pubs[0], mc_pubs[1]),stdd,color='y')
ax = pp_pubs.plot(get_ax=True, title='Standard Distance Circle', window=True, hull=True)
ax.add_artist(circle2)
plt.plot(mc_pubs[0], mc_pubs[1], 'r^', label='Mean Center')
ax.set_aspect('equal')
plt.legend(numpoints=1)

### <a id="Task 4">Task 4</a>
Please get your code below to plot the london pubs' mean center and the standard distance circle, with convex hull presented.

## <a id="Density Estimates">Density Estimates</a>
Through your practices last term on Statistics module, you might already familiar with one density estimation technique:**histogram**, by visualizing the definition of data bins, and the tallied number of data points within each bin; however, its choice of binning can have a disproportionate effect on visualization, hence smoother density estimates using various kernels will be powerful in modeling the distribution of points. 

The most commonly used kernel density estimate is Gaussian kernel density estimate, in which each point contributes a Gaussian curve to the total. These algorithms could be found both in [scikit-learn](http://scikit-learn.org/stable/) and in [PySAL](http://pysal.readthedocs.io/en/latest/). In scikit-learn it is implemented in the `classification` section at `sklearn.neighbors.KernelDensity estimator`, which uses the Ball Tree or KD Tree for efficient queries. I had included a map here to sklearn's algorithms and how to navigate them:

<a href="http://scikit-learn.org/stable/tutorial/machine_learning_map/"><img alt="SciKit-Learn Algorithm Map" src="http://scikit-learn.org/stable/_static/ml_map.png"></a>

While in `PySAL` it will be called from the Python Spatial Analysis Library. PySAL is similarly complex and _also_ has a map to help you navigate its complexities:

![PySAL Map](http://darribas.org/gds_scipy16/content/figs/pysal.png)

But I can't tell you which is the 'right' approach (as I said above) so far, as it all depends on what you're trying to accomplish and how you're _reasoning_ about your problem. 

### <a id="Quadrat Based Statistics">Quadrat Based Statistics</a>

As introduced in lecture, `CSR` process has two prominent characteristics: `Uniform` and `Independent`, which will help us to tell a `non-CSR` process by using Quadrat-based statistics. Against the null hypothesis of a `CRS` process, the expected point intensity $\lambda$ is uniform across the whole study area $\Re$, so the number of points within a sub-region $|A|$ should be $\lambda |A|$. 

If we further define the window $|A|$ as a $m \times n$ rectangular, then for a `CRS` process, the observed number of points within $|A|$ could be compared against the expected point counts using $\chi^2$ test statistic:

$$\chi^2 = \sum^m_{i=1} \sum^n_{j=1} \frac{[x_{i,j}-E(x_{i,j})]^2}{\lambda |A_{i,j}|}$$

* For a $\chi^2$ distribution with $m \times n -1$ degree of freedom, $p$-value could be derived from the $\chi^2$ distribution table; and the the null hypothesis will be rejected at the $95\%$ confidence level if $p$-value is smaller than $0.05$.

* For sampling distribution simulations from a large number of $\chi^2$ test statistics, under the null hypothesis of `CRS` process, if the $\chi^2$ test statistic for the observed point pattern is among the largest $5%$ test statistics, then it is very unlikely to be result of a `CSR` process at $95\%$ confidence level. Hence the null hypothesis is rejected followed by a pseudo $p$-value calculation. 
$$p(\chi^2) = \frac{1+\sum^{nsim}_{i=1}\phi_i}{nsim+1}$$
where 
$$ 
\phi_i =
 \begin{cases}
    1       & \quad \text{if } \psi_i^2 \geq \chi^2 \\
    0       & \quad \text{otherwise } \\
  \end{cases}
$$

$nsim$ is the number of simulations, $\psi_i^2$ is the $\chi^2$ test statistic for each simulated point pattern, $\chi^2$ is the $\chi^2$ test statistic for the observed point pattern, $\phi_i$ is an indicator variable.

In [99]:
pp_pubs.plot(window= True, title= "London Pubs Point pattern")

In [100]:
q_r_pubs = qs.QStatistic(pp_pubs,shape= "rectangle",nx = 4, ny = 4)
q_r_pubs.plot() # plot out the quadrat count figure with 4*4 windows

Can you figure out the meanings of number in each window? It shows directly the counts of points in each window.

In [101]:
print('Chi-squared test statistic for the observed point pattern is: '+ str(q_r_pubs.chi2)) 
print('Degree of freedom is: '+str(q_r_pubs.df)) 
print('P-valus for Chi-squared test statistic is: '+str.format('{0:.6f}', q_r_pubs.chi2_pvalue)) # 6 decimals

Chi-squared test statistic for the observed point pattern is: 6120.150734192389
Degree of freedom is: 15
P-valus for Chi-squared test statistic is: 0.000000


Since the $p$-value based on the analytical $\chi^2$ distribution (degree of freedom = 15) is 0.000000, much smaller than 0.05. We might reject the null hypothesis of being a `CSR` process.

Seconday, let's use hexagon quadrats as windows.

In [4]:
q_h_pubs = qs.QStatistic(pp_pubs,shape= "hexagon",lh =0.08) # lh is the length of hexagon edge, adjustable
q_h_pubs.plot()

KeyboardInterrupt: 

### <a id="Task 5">Task 5</a>
Get the statistics testing result for Hexagon window printed below, and conclude whether we should reject the `CSR` hypothesis? Is the distribution of pubs in London random or not?

In [1]:
# your code here
print('Chi-squared test statistic for the observed point pattern is: '+ str(q_h_pubs.chi2)) 
print('Degree of freedom is: '+str(q_h_pubs.df)) 
print('P-valus for Chi-squared test statistic is: '+str.format('{0:.6f}', q_h_pubs.chi2_pvalue)) 

NameError: name 'q_h_pubs' is not defined

Since the p-value is 0.00000 much smaller than 0.05, we reject the null hypothesis of CSR, and think the point pattern for London pubs is not random. 

You may find the summary reported the **Bounding Rectangle** and the **Area of window** for the London Pubs point pattern. As we passed it to the `PointPatterns` constructor the 3337 points' data for London pubs, `PySAL` finds the [minimum bounding box](https://en.wikipedia.org/wiki/Minimum_bounding_rectangle) and uses it as the window. So the area of window is simply the area of the bounding rectangle. 

### <a id="Window attributes & methods">Window attributes & methods</a>

In [8]:
pp_pubs.window.area

2382269775.688118

In [9]:
pp_pubs.window.centroid

(531520.9778137526, 178455.2195512079)

In [10]:
pp_pubs.window.bbox

[503922.2971398517, 156875.6574352089, 559119.6584876511, 200034.78166720615]

You may get a bounding box been given from left to bottom, then from right to top.

The `parts` for `window` is a list of polygons. Now let's check the point containment for the `window`. For example, I want to check whether The Edgar Wallace (with lat and lon at -0.112875 and 51.512704) is contained in this `window`, the test will return a boolean output.

In [ ]:
pp_pubs.window.contains_point((-0.112875, 51.512704)) # The Edgar Wallace contained in the window

In [11]:
pp_pubs.window.parts # We will introduce the concept of parts in later section

[[(503922.2971398517, 156875.6574352089),
  (503922.2971398517, 200034.78166720615),
  (559119.6584876511, 200034.78166720615),
  (559119.6584876511, 156875.6574352089),
  (503922.2971398517, 156875.6574352089)]]

The total rows add up to 3337, indicating 3337 pubs as our point targets. What else information you can derive from the summary of london pubs point data? Can you write down your answers to following questions:
1. What are the coordinates for the vertices of bounding rectangle? **---------------------**

2. What is the area of bounding rectangle window?**---------------------**

3. What is the estimated intensity of pubs for this rectangle window?**---------------------**

**Hint**: these will be used to compare with point intensity estimates results.

In [6]:
# Check the attributes of point patterns
pp_pubs.points

x              y
0     528800.702119  182217.050649
1     529328.933580  182215.263524
2     525023.754279  190707.360848
3     524930.433371  190565.524264
4     526240.508060  192213.278298
...             ...            ...
3332  527239.892173  181162.209482
3333  534648.747466  169365.026616
3334  535296.141482  183886.921206
3335  534850.134287  183592.155340
3336  533944.598958  191978.935679

[3337 rows x 2 columns]

### <a id="Point Intensity Estimates">Point Intensity Estimates</a>
The Point intensity is the mean number of event points per unit of area at given point $p_j$, and can be defined as:

$$\lambda(p_j) = \lim \limits_{|\mathbf{A}p_j| \to 0} \left \{ \frac{E(Y(\mathbf{A}p_j)}{|\mathbf{A}p_j|} \right \}   $$

where $\mathbf{A}p_j$ is a region surrounding location $p_j$ with area $|\mathbf{A}p_j|$, and $E(Y(\mathbf{A}p_j)$ is the expected number of event points in $\mathbf{A}p_j$. 

We may recall one of the implications of CSR process last week, that its point intensity is constant in study area $\Re$, which could be expressed as:

$\lambda(p_j) = \lambda(p_{j+1}) = \ldots = \lambda(p_n) = \lambda \ \forall p_j \in \Re$. Thus, if the area of $\Re$ = $|\Re|$, the expected number of event points in the study region is: $E(Y(\Re)) = \lambda |\Re|.$

Last week, you've already been introduced the concept of `Convex Hull` (the smallest convex set that contains a point pattern) and `Minimum Bounding Rectangle (Box)` (the minimum bounding Rectangle, bigger than convex hull) for Shape Analysis. They could fit into the general concept of `window`.

In PySAL, it is estimated by using a geometric object to encode the study region, which is the so-called "window", $W$, as introduced in last practical. The reason for distinguishing between $\Re$ and $W$ is that the latter permits alternative definitions of the bounding object as:

$$\hat{\lambda} = \frac{n}{|W|}$$

where $n$ is the number of points in the *window* $W$, and $|W|$ is the area of $W$. 

You may recap on what we've practiced last week covered a bit on the function of minimum bounding box:

$$\hat{\lambda}_{mbb} = \frac{n}{|W_{mbb}|}$$

where $W_{mbb}$ is the minimum bounding box for the point pattern. Now let's try to understand the definition by using London pubs point dataset.

#### Minimum bounding box
Now we will call the minimum bounding box function as `lambda_mbb`, to get the estimated density of pub points within the defined window.

In [28]:
# number of pubs if within minimum bounding box window
print (pp_pubs.lambda_mbb * pp_pubs.mbb_area)

3337.0


What you've got? Is it exactly same with the above summary result at 10834.35...? YES, you will find the minimum bounding box for london pubs is exactly the rectangle window of greater London! It means based on current pubs density in London, if we take the whole area of the rectangle bounding window, then the estimated pubs in Greater London will reach at 10834 (or 1 more!), which is more than 3337 pubs so far, and a much densier calculated distribution of pubs will be expected.

Let's further check the coordinates for bounding rectangle from summary by using Google Map. What have you returned with this time? If you find them as $Ripley$ and $Stondon Massey$, then you had successfully locate the left-bottom and right-top for the bounding rectangle, which is also the boundary for Greater London. 

####  Convex hull
Besides of the rectangle window, we want a shapely closer window. So we can recall the concept of `convex hull` introduced last week, and express the point intensity as:

$$\hat{\lambda}_{hull} = \frac{n}{|W_{hull}|}$$

where $W_{hull}$ is the convex hull for the point pattern.

In [27]:
# number of pubs if within convex hull window
print (pp_pubs.lambda_hull * pp_pubs.hull_area)

3336.9999999999995


As the area of the window decreased by its getting closer to the London boundary, the estimated pubs number reduced to 14802, but still approximately 3 times more than the real value. 

We can conclude that, point density estimation is very sensitive to the **area of study region** (or we term it as "window" here) as introduced in lecture, hence geographical **scale** is cucial when we conduct point pattern analysis.

These varied windows help to build up our statistics. This is actually the elementary basis for generating **heatmap**. So has it reminded you any idea of a high quality interactive heatmap for london pubs?

## <a id="Heatmap of London Pubs">Heatmap of London Pubs</a>
To realize the heatmap function, we need to recall your memory on how to generating the heatmap for crime data last term. **Hint**: Use `folium`.

In [31]:
# use geopandas to read london pubs shapefile data
# your code here
pubs_gdf=gpd.read_file('data/London_Pubs/London_Pubs.shp')

In [35]:
# We call folium to realize interactive heatmap of London pubs
import folium
from folium import plugins
from folium.plugins import HeatMap, MarkerCluster, FastMarkerCluster
# Ensure you're handing it floats
pubs_gdf['lat'] = pubs_gdf['latitude'].astype(float)
pubs_gdf['lon'] = pubs_gdf['longitude'].astype(float)

# Filter the DF for rows, then columns, then remove NaNs
heat_df = pubs_gdf[['lat', 'lon']]
heat_df = heat_df.dropna(axis=0, subset=['lat','lon'])

# List comprehension to make out list of lists
heat_data = [[row['lat'],row['lon']] for index, row in heat_df.iterrows()]

heatmap_map = folium.Map([51.50632, -0.1271448], zoom_start=12)

# Plot it on the map
hm=plugins.HeatMap(heat_data)
heatmap_map.add_child(hm)
# get the map shown below 
# if it is blank for browser reason, please save it as html file
heatmap_map

Can you try to zoom in/out with the heatmap you've got, and find the densiest part of pubs in London? In addition, what's the rationale of `HeatMap` function in `folium`, especially its density basis? Try google it.

This is straightforward and fancinating, however if we want to know more about the pubs' density in each losa, how we are going to deal with it? 

Think about the "Window" concept, each LSOA could be taken as one sub window defined by administrative boundary, so the measure for density of pubs in each losa is actually to count the number of points (pubs) in each polygon (lsoa) with varied shapes. The starting point should be joining the pubs and lsoas datasets together, by recalling the joining function introduced in week 2 and week 3. 

**Hint**: We need to get the columns names listed for both datasets and find the shared column (or rename relevant column for indexing convenience) to realize the data joining.

In [38]:
# Your code here
pubs_gdf.columns

Index(['F1', 'name', 'latitude', 'longitude', 'lsoa', 'strNearest',
       'intNearest', 'bakerloo', 'circle', 'hammersmit', 'jubilee', 'victoria',
       'central', 'district', 'east_londo', 'metropolit', 'northern',
       'piccadilly', 'waterloo_a', 'dlr', 'F21', 'id', 'latitude1',
       'longitude1', 'name1', 'display_na', 'zone', 'total_line', 'rail',
       'geometry', 'lat', 'lon'],
      dtype='object')

In [39]:
# use geopandas to read london lsoas shapefile data
lsoas_gdf=gpd.read_file('data/LSOA_IMD2019.shp')
lsoas_gdf.head()

objectid   lsoa11cd                   lsoa11nm                  lsoa11nmw  \
0         1  E01000001        City of London 001A        City of London 001A   
1         2  E01000002        City of London 001B        City of London 001B   
2         3  E01000003        City of London 001C        City of London 001C   
3         4  E01000005        City of London 001E        City of London 001E   
4         5  E01000006  Barking and Dagenham 016A  Barking and Dagenham 016A   

      st_areasha   st_lengths  IMD_Rand  IMD_Decile  \
0  133320.768872  2291.846072     29199           9   
1  226191.272990  2433.960112     30379          10   
2   57302.966538  1142.359799     14915           5   
3  190738.760504  2167.868343      8678           3   
4  144195.846857  1935.510354     14486           5   

                    LSOA01NM      LADcd  ... OutRank  OutDec  TotScore  \
0        City of London 001A  E09000001  ...    1615       1      1296   
1        City of London 001B  E09000001  ...    2969       1      1156   
2        City of London 001C  E09000001  ...     162       1      1350   
3        City of London 001E  E09000001  ...     849       1      1121   
4  Barking and Dagenham 016A  E09000002  ...    4368       2      2040   

   TotRank  TotDec  DepChi  Pop16_59         Pop60_      WorkPop  \
0      175     656     465    715.00  343907.419830  3682.439420   
1      182     580     394    619.75  583474.041779  3910.387240   
2      146     759     445    804.00  147839.506081  1834.931320   
3      229     692     200    683.00  491918.093037  3483.179208   
4      522    1297     221   1284.50  372257.321186  3108.610781   

                                            geometry  
0  POLYGON ((532095.563 181577.351, 532095.125 18...  
1  POLYGON ((532267.728 181643.781, 532262.875 18...  
2  POLYGON ((532105.312 182010.574, 532104.872 18...  
3  POLYGON ((533610.974 181410.968, 533615.622 18...  
4  POLYGON ((544817.826 184346.261, 544815.791 18...  

[5 rows x 67 columns]

Have you decided which column should be used for joining? Yes, the "lsoa" and "lsoa11nm". But you may observed there are many columns we don't need so far, hence we could keep the columns needed; also it is better to rename the remaining columns for convenience. 

In [40]:
lsoas_gdf = lsoas_gdf[['lsoa11cd', 'lsoa11nm', 'st_areasha', 'geometry']]
colnames = ['code','lsoa','area','geometry']
lsoas_gdf.columns = colnames
lsoas_gdf.head(4)

code                 lsoa           area  \
0  E01000001  City of London 001A  133320.768872   
1  E01000002  City of London 001B  226191.272990   
2  E01000003  City of London 001C   57302.966538   
3  E01000005  City of London 001E  190738.760504   

                                            geometry  
0  POLYGON ((532095.563 181577.351, 532095.125 18...  
1  POLYGON ((532267.728 181643.781, 532262.875 18...  
2  POLYGON ((532105.312 182010.574, 532104.872 18...  
3  POLYGON ((533610.974 181410.968, 533615.622 18...

### <a id="Task 6">Task 6</a>
We want to realize the following purposes and you need to replace the question marks with reasonable codes.
1. count the total number of pubs within each lsoa, ensure the data type is integer, and reset the index.
2. join the lsoas and newly generated count datasets together, and save it as shapefile, get it plotted with raw count number.
3. calculate the density of pubs in each lsoa and get it plotted.

In [41]:
# calculating total number of pubs per lsoa
lsoas_pubs_count = pd.DataFrame(pubs_gdf['lsoa'].value_counts().astype(int)).reset_index()
# only leave the 2 columns for plot generating
lsoas_pubs_count.columns = ['lsoa','Numbers']
lsoas_pubs_count.head(4)

lsoa  Numbers
0  City of London 001F      103
1  City of London 001G       40
2     Westminster 018A       36
3     Westminster 013B       36

In [43]:
# add a new column of pubs number in each lsoa 
# by join lsoa and pubs through attribute join
join_gdf = lsoas_gdf.merge(lsoas_pubs_count, on='lsoa')
# save this newly joined .csv file into lsoa_numbers.shp file
# your code here
join_gdf.to_file('data/lsoa_numbers.shp')
# Make a Choropleth map on pubs per lsoa.
join_gdf.plot(column='Numbers', cmap='coolwarm', scheme='quantiles', alpha=0.7, legend=True)

The output looks quite different from the point pattern presented in heatmap, what is the problem?
The output shows us the raw count data in each lsoa, without taking into account of the area of each window, which means if we want the density map, we need to divide the numbers of pubs by area of the lsoa.

In [44]:
# check the data format, and think of why we need multiple 100000
join_gdf['density'] = join_gdf.apply(lambda row: 100000*row.Numbers / row.area, axis=1)
join_gdf.plot(column='density', cmap='coolwarm', scheme='quantiles', alpha=0.7, legend=True)

Is it much similar with the heatmap point pattern now? 

##  <a id="Finding Nearest Neighbors">Finding Nearest Neighbors</a>

We will divide this section into two parts with 2 datasets used for each: **London pubs data** will be used in part 1 to understand the theoretical basis of nearest neighbors and K nearest neighbors; **London Airbnb data** will be used in part 2 for realization of K nearest neighbors classification and visualization.

$Part 1$:

In theory, neighbors-based methods are known as non-generalizing machine learning methods, and there are many learning routines relying on nearest neighbors at their core. The working mechanism is that, they try to “remember” all of its training data (possibly transformed into a fast indexing structure such as a `Ball Tree` or `KD Tree`), build up the distance metrics through searching the distances between targeted point and its neighbors, and get the results of nearest neighbor point to each targeted point, as well as the corresponding distance. It can be realized through calling `NearestNeighbors` in `sklearn.neighbors`, with input data as either `NumPy` arrays or scipy.sparse matrices (the latter doesn't work for our data), and outputs as indices for the nearest neighbor to each point, together with respective distance. 

We will start our understanding of the distance-based methodology with a "small dataset", **London pubs data**, to get nearest neighbors and the relevant distance based statistical methods.
* [Nearest Neighbors](#Nearest-Neighbors)
* [Mean Nearest Neighbor Distance Statistics](#Mean-Nearest-Neighbor-Distance-Statistics)
* [K Nearest Neighbors (KNN)](#K-Nearest-Neighbors-(KNN))

$Part 2$:

In practice, the K-nearest neighbor algorithm  was mostly used for classification, given a positive integer $K$, to search for the major vote between the $K$ most similar instances to a given “unseen” observation $x$. It firstly runs through the whole dataset computing a similarity metric $d$ between $x$ and each training observation (the samples); a set consisting of $K$ closest points to $x$ will be get; then it estimates the conditional probability for each class, which is the proportion of points in the generated set with corresponding class label; at last, the observation $x$ gets assigned to the class with largest probability. We will change into a "larger dataset", **London Airbnb data**, to train defined sample data using default *uniform weights*(assigns uniform weights to each query neighbor from a simple majority "vote" of the nearest neighbors). To realize this goal, we will use `Bokeh` for visulization, and call `Scikit-learn` on **K Neighbors Classifier**: based on the $k$ (integer value, specified by you) nearest neighbors of each query point in the training sample, it is the most commonly used technique. In general, larger $k$ can help to suppress the effects from noise, whilst smaller $k$ can help to make the classification boundaries more distinct. 

### <a id="Nearest Neighbors">Nearest Neighbors</a>
One can use the `KDTree` or `BallTree` classes directly to find nearest neighbors. This is the functionality wrapped by the NearestNeighbors class. The Ball Tree and KD Tree have the same interface; we’ll show an example of using the `BallTree` here, and let you do the task by using `KDTree`.

In [5]:
from sklearn.neighbors import NearestNeighbors
import fiona
from shapely.geometry import shape

pp_pubs_2 = fiona.open('data/London_pubs/London_pubs.shp') # read the london pubs point shapefile data
geoms = [ shape(feat['geometry']) for feat in pp_pubs_2 ] # read the geometry
pp_pubs_arrays = [ np.array((geom.xy[0][0], geom.xy[1][0])) for geom in geoms ] # turn points into point array

In [6]:
nbrs = NearestNeighbors(n_neighbors=2, algorithm='ball_tree').fit(pp_pubs_arrays) # use ball_tree
distances, indices = nbrs.kneighbors(pp_pubs_arrays)

In [7]:
indices 

array([[   0, 1098],
       [   1, 1163],
       [   2,    3],
       ...,
       [3334, 1054],
       [3335, 2607],
       [3336, 2733]])

In [8]:
distances

array([[0.        , 0.00085529],
       [0.        , 0.00113044],
       [0.        , 0.00187763],
       ...,
       [0.        , 0.00387549],
       [0.        , 0.00226028],
       [0.        , 0.00175393]])

Because the query set matches the training set, the nearest neighbor of each point is the point itself, at a distance of zero.
It is also possible to efficiently produce a sparse graph showing the connections between neighboring points:

In [9]:
nbrs.kneighbors_graph(pp_pubs_arrays).toarray()

array([[1., 0., 0., ..., 0., 0., 0.],
       [0., 1., 0., ..., 0., 0., 0.],
       [0., 0., 1., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 1., 0., 0.],
       [0., 0., 0., ..., 0., 1., 0.],
       [0., 0., 0., ..., 0., 0., 1.]])

###  <a id="Task 7">Task 7</a>
Can you get the nearest neighbors for London pubs by using KDTree? Your code below:

In [10]:
# use kd_tree
nbrs_kd = NearestNeighbors(n_neighbors=2, algorithm='kd_tree').fit(pp_pubs_arrays) # use ball_tree
distances_kd, indices_kd = nbrs_kd.kneighbors(pp_pubs_arrays)
# indices

In [11]:
distances_kd # distances

array([[0.        , 0.00085529],
       [0.        , 0.00113044],
       [0.        , 0.00187763],
       ...,
       [0.        , 0.00387549],
       [0.        , 0.00226028],
       [0.        , 0.00175393]])

### <a id="Mean Nearest Neighbor Distance Statistics">Mean Nearest Neighbor Distance Statistics</a>

$$\bar{d}_{min}=\frac{1}{n} \sum_{i=1}^n d_{min}(s_i)$$

It is the average of all the points and corresponding distances demonstrated by Clark and Evans(1954), as a normal distribution under null hypothesis (CSR process). The distances between the nearest neighbor(s) $N(p)$ and the point $p$ is nearest neighbor distance for $p$, which meet the condition
$$d_{p,N(p)} \leq d_{p,j} \forall j \in S - p$$

Hence the test statistics could be used to determine whether the point pattern is CSR, cluster or regular spatial process. For example, we can call the method `knn` to find $k$ nearest neighbors for each pub point in the point pattern *pp_pubs*. The first array is the most nearest neighbor for each pub point, the second array is the distance between each pub point and its nearest neighboring pub.

In [55]:
# one nearest neighbor
pp_pubs.knn()

(array([[1098],
        [3191],
        [   3],
        ...,
        [1054],
        [2607],
        [2733]]), array([[ 67.17132152],
        [103.29035554],
        [169.78341619],
        ...,
        [275.02359024],
        [187.57469078],
        [195.08124671]]))

In [56]:
# two nearest neighbors
pp_pubs.knn(2)

(array([[1098, 2969],
        [3191, 3192],
        [   3, 1471],
        ...,
        [1054, 1946],
        [2607, 2984],
        [2733, 2987]]), array([[  67.17132152,  117.60354309],
        [ 103.29035554,  116.40093361],
        [ 169.78341619, 1594.52131725],
        ...,
        [ 275.02359024,  377.173317  ],
        [ 187.57469078,  459.01627843],
        [ 195.08124671,  346.33946903]]))

In [57]:
pp_pubs.nnd # Nearest neighbor distances

array([[ 67.17132152],
       [103.29035554],
       [169.78341619],
       ...,
       [275.02359024],
       [187.57469078],
       [195.08124671]])

In [58]:
pp_pubs.max_nnd # Maximum nearest neighbor distance

2268.018767301039

In [59]:
pp_pubs.min_nnd # Minimum nearest neighbor distance

0.0

In [60]:
pp_pubs.mean_nnd # mean nearest neighbor distance

221.81179983959822

From above, we may conclude that the principle behind nearest neighbor methods is distance based (most commonly use `Euclidean distance`), to find a specified **number** of "training" samples closest to the target point (which is "unseen" in real case), and try to predict the label for the target from samples. So the **number** here could be a constant defined by us (for example, K nearest neighbors), or varied number based on local points density. 
### <a id="K Nearest Neighbors (KNN)">K Nearest Neighbors (KNN)</a>

**KNN** is a non parametric and instance-based algorithm, and is normally used in a supervised learning setting for classification purpose. With a dataset of training observations $(x,y)$, where $x$ denotes the feature and $y$ denotes the target, we want to capture the relationship between $x$ and $y$ for prediction purpose. This algorithm is similarly defined according to a distance metric between two data points, which we are familiar with, and choosing the popular Euclidean distance by


$$d(x,x') = \sum^n_{i=1} \sqrt{(x_1-x'_1)^2+(x_2-x'_2)^2+......+(x_n-x'_n)^2}$$




PySAL weights can be constructed easily from many ways, i.e. array, shapefile and dataframe. For this practical, we are going to construct the weights directly from pandas and geopandas using the .from_shapefile and .from_dataframe method. Although we will still use points data for this practical, but it is better to know that if it is polygon data, then centroid points will be used by default.

#### <a id="k-nearest neighbor weights">k-nearest neighbor weights</a>

The neighbors for a given observations can be defined using a k-nearest neighbor criterion, to create nearest neighbor weights matrix based on k nearest neighbors' distances. Based on our dataset, we can either build a knn weights directly from the london pubs shapefile, or implement it through dataframe. Please refer to https://pysal.org/pysal/generated/pysal.lib.weights.KNN.html for further information. Let's take $k=8$ as an example:

In [61]:
wknn_shp = ps.lib.weights.KNN.from_shapefile(('data/london_pubs/london_pubs.shp'), k=8)
wknn_shp.neighbors[0]

[1098, 2969, 2501, 917, 923, 1253, 1235, 2647]

#### <a id="Distance band weights">Distance band weights</a>

Knn weights ensure that all observations have the same number of neighbors. The distance bands weights define the neighbor set for each spatial unit as those other units falling within a threshold distance of the focal unit, so the number of neighbours is very likely to vary across observations with distance band weights. They can be generated for shapefiles and arrays of points with the starting point at determining the minimum nearest neighbour distance.

In [12]:
thresh = ps.lib.weights.min_threshold_dist_from_shapefile('data/london_pubs/london_pubs.shp')

In [13]:
print(thresh)

0.026317545168575214


with this threshold in hand, the distance band weights are obtained as:

In [14]:
wband = ps.lib.weights.DistanceBand.from_shapefile('data/london_pubs/london_pubs.shp', threshold=thresh, binary=True)
print(wband.min_neighbors)
# wband = ps.lib.weights.DistanceBand.from_dataframe(pubs_gdf, threshold=thresh, binary=True)
print(wband.max_neighbors)

1
543


In [73]:
wband.histogram

[(1, 12),
 (2, 5),
 (3, 18),
 (4, 19),
 (5, 24),
 (6, 27),
 (7, 28),
 (8, 22),
 (9, 29),
 (10, 36),
 (11, 44),
 (12, 37),
 (13, 43),
 (14, 34),
 (15, 27),
 (16, 22),
 (17, 38),
 (18, 46),
 (19, 27),
 (20, 37),
 (21, 24),
 (22, 27),
 (23, 33),
 (24, 37),
 (25, 45),
 (26, 28),
 (27, 27),
 (28, 23),
 (29, 22),
 (30, 27),
 (31, 21),
 (32, 17),
 (33, 15),
 (34, 14),
 (35, 18),
 (36, 10),
 (37, 14),
 (38, 18),
 (39, 25),
 (40, 16),
 (41, 30),
 (42, 22),
 (43, 23),
 (44, 18),
 (45, 17),
 (46, 17),
 (47, 16),
 (48, 22),
 (49, 22),
 (50, 21),
 (51, 24),
 (52, 17),
 (53, 22),
 (54, 24),
 (55, 21),
 (56, 19),
 (57, 23),
 (58, 17),
 (59, 15),
 (60, 18),
 (61, 20),
 (62, 8),
 (63, 15),
 (64, 11),
 (65, 7),
 (66, 6),
 (67, 9),
 (68, 10),
 (69, 14),
 (70, 11),
 (71, 11),
 (72, 11),
 (73, 12),
 (74, 14),
 (75, 21),
 (76, 12),
 (77, 12),
 (78, 13),
 (79, 10),
 (80, 9),
 (81, 19),
 (82, 12),
 (83, 10),
 (84, 12),
 (85, 6),
 (86, 8),
 (87, 12),
 (88, 5),
 (89, 11),
 (90, 5),
 (91, 11),
 (92, 12),
 (93, 1

#### <a id="Kernel weights">Kernel weights</a>

This is a combination of distance-based thresholds together with continuously valued weights supported through kernel weights. The bandwidth attribute plays the role of the distance threshold with kernel weights, while the form of the kernel function determines the distance decay in the derived continuous weights (e.g.,‘triangular’,’uniform’,’quadratic’,’epanechnikov’,’quartic’,’bisquare’,’gaussian’). All kernel methods also support construction from shapefiles with Kernel.from_shapefile, and from dataframes with Kernel.from_dataframe.

In the following example, we will use the default bandwidth setting as fixed across the observations.However you may set it into adaptive bandwidth by turning off the default 'fixed' upon your requirements.
More details on kernel weights can be found in Kernel (https://pysal.org/pysal/generated/pysal.lib.weights.Kernel.html).

In [78]:
kw = ps.lib.weights.Kernel.from_dataframe(pubs_gdf, fixed = True, function = 'gaussian')

In [79]:
kw.weights[0]

[0.24766677199898607,
 0.24801420832345297,
 0.25037508657626656,
 0.24856756156823195,
 0.24311517298658983,
 0.2710141753831345,
 0.2666631124071554,
 0.24989783129796433,
 0.2907769222922916,
 0.29491444588103694,
 0.28165700224021983,
 0.2928883813128274,
 0.28941034312684927,
 0.292324532670166,
 0.2643901551687217,
 0.2970273525865374,
 0.30470785073949125,
 0.24210591052773833,
 0.2951005254983616,
 0.2624126126335426,
 0.25790401630181464,
 0.2753371121964674,
 0.2704201122302546,
 0.2670521591215724,
 0.32529457149373475,
 0.286231592671268,
 0.2807970054142671,
 0.28211168025290234,
 0.31201812125218653,
 0.25758186369959113,
 0.26351804155950725,
 0.24222114248515914,
 0.2503699336433758,
 0.24973016516522026,
 0.27437483146702973,
 0.27645774922548955,
 0.3205689511268098,
 0.3102237183435842,
 0.2525243228608511,
 0.281747210030458,
 0.27397990752115514,
 0.27724917210068545,
 0.26764166619837154,
 0.2590030443527725,
 0.2988741319765257,
 0.2989681697907711,
 0.2928576570

In [80]:
kw.bandwidth

array([[0.05458538],
       [0.05458538],
       [0.05458538],
       ...,
       [0.05458538],
       [0.05458538],
       [0.05458538]])

### <a id="Task 8">Task 8</a>

Summarize the aforementioned 3 .from_dataframe methods below, and compare their outputs using the LSOA_IMD2019 dataset. 

In [85]:
import geopandas as gpd
lsoadf = gpd.read_file('data/LSOA_IMD2019.shp')
wknn_lsoa = ps.lib.weights.KNN.from_dataframe(lsoadf, k=5) # k value may vary
kw_lsoa = ps.lib.weights.Kernel.from_dataframe(lsoadf, fixed=True, function='gaussian')
thresh = ps.lib.weights.min_threshold_dist_from_shapefile('data/LSOA_IMD2019.shp')
dbb_lsoa = ps.lib.weights.DistanceBand.from_dataframe(lsoadf, binary=False, threshold=thresh) # distance based weight, binary is set as False
dbc_lsoa = ps.lib.weights.DistanceBand.from_dataframe(lsoadf, binary=True, threshold=thresh) # distance based weight, binary is set as True

print(wknn_lsoa.neighbors[0])
print(kw_lsoa.neighbors[0])
print(dbb_lsoa.neighbors[0])
print(dbc_lsoa.neighbors[0])

[1, 2]
[3038, 3901, 4611, 4612, 901, 4613, 4615, 4893, 4894, 2946, 2947, 2948, 3042, 3043, 3044, 4772, 4774, 3040, 3845, 3855, 4779, 4782, 4783, 4784, 3841, 3843, 3844, 3849, 4773, 2949, 2950, 3846, 3847, 4614, 832, 833, 836, 926, 927, 4594, 4640, 4641, 834, 835, 837, 897, 900, 919, 923, 924, 925, 932, 933, 934, 936, 937, 940, 920, 921, 935, 938, 2647, 2648, 2649, 2653, 896, 898, 899, 902, 918, 922, 2663, 2664, 4786, 0, 2, 2642, 2644, 2661, 2662, 4860, 4861, 2633, 2634, 2635, 2636, 2639, 2652, 2665, 2666, 2667, 1736, 1739, 2641, 2645, 2737, 2738, 2727, 2728, 2729, 2732, 2734, 2735, 2736, 2646, 2637, 2638, 2650, 2730, 2731, 2655, 2657, 2658, 2710, 2725, 2726, 3872, 3880, 3854, 3870, 3871, 3887, 3848, 3850, 3851, 3852, 3853, 4781, 4818, 3885, 3886, 3888, 3883, 3884, 3930, 4777, 4778, 4820, 3, 3842, 3889, 3929, 4186, 4187, 4780, 4785, 4793, 4794, 3926, 3927, 4184, 4185, 4188, 4189, 4193, 4194, 4196, 4211, 4190, 4191, 4192, 1, 2640, 2643, 4917, 4198, 4199, 4201, 4202, 4204, 4207, 4208, 420

## <a id="Nearest Neighbors Classification Visualization">Nearest Neighbors Classification Visualization<a/>
Nearest neighbors classification realizes classification by training defined sample data using specified weights. So the configuration of **weights** are crucial in neareast neighbours classification, and we normally use default *uniform weights*, where the value setting of weights keywords is:**weights = 'uniform'** (assigns uniform weights to each query neighbor from a simple majority "vote" of the nearest neighbors). You may also found another definition of weights by distance as **weights = 'distance'** (assigns weights proportional to the inversed distance from the query point). 

Upon the your clear setting of weights, we can call two types of nearest neighbors classifiers from `Scikit-learn`:
1. **K Neighbors Classifier**: based on the $k$ (integer value, specified by you) nearest neighbors of each query point in the training sample, it is the most commonly used technique. In general, larger $k$ can help to suppress the effects from noise, whilst smaller $k$ can help to make the classification boundaries more distinct.
2. **Radius Neighbors Classifier**: based on the number of neighbors within a radius $r$ (fixed, floating-point data, specified by you) of each point in the training sample. Rarely used and specialized for not uniformly sampled data, so you should get the "curse of dimensionality" problem in mind if you need to use it.

For a better understanding and visualization of the classification results, we will hereby use London Airbnb data as the basis for analysis, call `K neighbors classifier` and try to use `Bokeh` for visulization. 

In [15]:
import seaborn as sns
terrain = sns.color_palette(palette='terrain',n_colors=10)
plasma = sns.color_palette(palette='plasma',n_colors=10)
rainbow = sns.color_palette(palette='rainbow',n_colors=6)

from bokeh.io import output_notebook
from bokeh.layouts import gridplot,row,column
from bokeh.plotting import figure,show
output_notebook()

Loading BokehJS ...

Bokeh is a powerful data visualization library, you may want to explore its wide application at [Bokeh website](https://bokeh.pydata.org/en/latest/).

In [16]:
# read the dataset for airbnb listings as training dataframe
traindf = pd.read_csv('data/airbnb_listings.csv')
traindf.head()

id                         listing_url       scrape_id last_scraped  \
0  11551  https://www.airbnb.com/rooms/11551  20191105115249   2019-11-06   
1  38151  https://www.airbnb.com/rooms/38151  20191105115249   2019-11-06   
2  13913  https://www.airbnb.com/rooms/13913  20191105115249   2019-11-06   
3  38407  https://www.airbnb.com/rooms/38407  20191105115249   2019-11-06   
4  90700  https://www.airbnb.com/rooms/90700  20191105115249   2019-11-06   

                                         name  \
0  Arty and Bright London Apartment in Zone 2   
1                         Double room/ lounge   
2         Holiday London DB Room Let-on going   
3           Canary Wharf Immaculate Apt for 2   
4           Sunny Notting Hill flat & terrace   

                                             summary  \
0  Unlike most rental apartments out there my fla...   
1                                                NaN   
2  My bright double bedroom with a large window h...   
3  The bright, light and stylish apartment in Can...   
4  This is a home not a hotel - for the cost gues...   

                                               space  \
0  Amenities Bedding: 1 Double bed, 1 living room...   
1  Comfortable, large double room /lounge area av...   
2  Hello Everyone, I'm offering my lovely double ...   
3  An entire bright, light and stylish apartment....   
4  This charming 1 bedroom with en-suite bathroom...   

                                         description experiences_offered  \
0  Unlike most rental apartments out there my fla...              family   
1  Comfortable, large double room /lounge area av...                none   
2  My bright double bedroom with a large window h...            business   
3  The bright, light and stylish apartment in Can...                none   
4  This is a home not a hotel - for the cost gues...                none   

                               neighborhood_overview  ... instant_bookable  \
0  Not even 10 minutes by metro from Victoria Sta...  ...                t   
1                                                NaN  ...                f   
2  Finsbury Park is a friendly melting pot commun...  ...                f   
3  Very easy to get to all the main sites. The tu...  ...                t   
4  A quick guide or a run through about the area ...  ...                t   

  is_business_travel_ready          cancellation_policy  \
0                        f  strict_14_with_grace_period   
1                        f                     flexible   
2                        f                     moderate   
3                        f  strict_14_with_grace_period   
4                        f  strict_14_with_grace_period   

  require_guest_profile_picture require_guest_phone_verification  \
0                             f                                t   
1                             f                                f   
2                             f                                f   
3                             f                                f   
4                             f                                f   

   calculated_host_listings_count  \
0                               2   
1                               1   
2                               2   
3                               1   
4                               2   

   calculated_host_listings_count_entire_homes  \
0                                            2   
1                                            0   
2                                            1   
3                                            1   
4                                            2   

  calculated_host_listings_count_private_rooms  \
0                                            0   
1                                            1   
2                                            1   
3                                            0   
4                                            0   

   calculated_host_listings_count_shared_rooms  reviews_per

Can you figure out the room types for Airbnb in London from this dataset?
As you may find, there are mainly 3 types of room types, Entire home/apt, Private room and Shared room (since 2019 there is a 4th type of Airbnb room called hotel room only took tiny proportion), so we will try to plot them by different colors below.

In [17]:
# set up the plot frame, 
# define x axis and y axis scales by the upper and lower limits of corresponding values
p = figure(title="London airbnb room types",y_range=(51.28,51.7),x_range=(-0.6,0.4))
p.xaxis.axis_label = 'longitude'
p.yaxis.axis_label = 'latitude'
# set up latitude and longitude variables for type of Private room
privateLat=traindf['latitude'][traindf['room_type']=='Private room']
privateLong=traindf['longitude'][traindf['room_type']=='Private room']
# set up latitude and longitude variables for type of Shared room
sharedLat=traindf['latitude'][traindf['room_type']=='Shared room']
sharedLong=traindf['longitude'][traindf['room_type']=='Shared room']
# set up latitude and longitude variables for type of Entire home/apt
entireLat=traindf['latitude'][traindf['room_type']=='Entire home/apt']
entireLong=traindf['longitude'][traindf['room_type']=='Entire home/apt']
# define different colors for each type
p.circle(privateLong,privateLat,size=3,color=terrain.as_hex()[1],fill_alpha=0.1,line_alpha=0.4,legend_label='Private room')
p.circle(sharedLong,sharedLat,size=3,color=plasma.as_hex()[9],fill_alpha=0.1,line_alpha=0.4, legend_label='Shared room')
p.circle(entireLong,entireLat,size=3,color=plasma.as_hex()[5],fill_alpha=0.1,line_alpha=0.4, legend_label='Entire home/apt')
show(p, notebook_handle=True)

You may already noticed that some buttons generated together with the plot on the right column. Try click on the buttons, and get the right way to zoom in certain areas in London. Of course, you also need to find your way back with another button. Once you zoomed in, you may find that areas e.g. near East Village, Chelsea, Hell's Kitchen, and Upper East Side, look brighter than the neighbors, indicating higher interest or more requests from Airbnb "hunters". In order to figure out which specific type of Airbnb really contribute to the distribution, we can plot them out by type separately.

In [18]:
# plot private room
p1 = figure(width=500, height=300, title='Private airbnb rooms distribution in London',y_range=(51.28,51.7),x_range=(-0.6,0.4))
p1.circle(privateLong,privateLat,size=3,color=terrain.as_hex()[1],fill_alpha=0.2,line_alpha=0.1,legend_label='Private room')
# plot shared room
p2 = figure(width=500, height=300, title='Shared airbnb rooms distribution in London',y_range=(51.28,51.7),x_range=(-0.6,0.4))
p2.circle(sharedLong,sharedLat,size=3,color=plasma.as_hex()[9],fill_alpha=0.2,line_alpha=0.1,legend_label='Shared room')
# plot entire home/apt
p3 = figure(width=500, height=300, title='Entire airbnb homes/apartments distribution in London',y_range=(51.28,51.7),x_range=(-0.6,0.4))
p3.circle(entireLong,entireLat,size=3,color=plasma.as_hex()[5],fill_alpha=0.2,line_alpha=0.1,legend_label='Entire home/apt')
# get plots show
show(column(p1,p2,p3), notebook_handle=True)

Now you may get some rough ideas on where are the hot airbnbs accummulating, are they normally around some popular venues, siteseeing places, etc.? Does an airbnb receiving high popularity in booking indicate the well acceptance from the customers? If so, how are other neighboring airbnb accommodations? To get the answers, we can use KNN as one of the optimal choices, and starting with creating dataframes from point coordinates data the dependent variable, which is **room_type**.

In [19]:
# loading the libraries
from matplotlib.colors import ListedColormap
from sklearn import neighbors, datasets
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import train_test_split
import scipy as sp

# define independant variable X with the points' coordinates
# define dependant variable y with room type
X = pd.concat([traindf['latitude'],traindf['longitude']],axis=1)
y = traindf['room_type']
h = .02  # step size in the mesh

# we'll split the training data into testing and training sets
# test_size is the proportion of dataset to include in the test split
# random_state is the count of seeds used by random number generator
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, random_state=45) 
# execute the classification, define k as 9
neigh = KNeighborsClassifier(n_neighbors=9)
neigh.fit(X_train, y_train)

KNeighborsClassifier(algorithm='auto', leaf_size=30, metric='minkowski',
                     metric_params=None, n_jobs=None, n_neighbors=9, p=2,
                     weights='uniform')

Upon classification, we can further predict the "unseen" room type, and check the capability of predication.

In [26]:
# define the predicted y value for tested X
predVal=neigh.predict(X_test)
# include both the predicted y value and real tested y value
mat=[predVal,y_test]
# read both into a single dataframe
testdf=pd.DataFrame(mat).transpose()

In [27]:
testdf.head()

0                1
0  Entire home/apt  Entire home/apt
1  Entire home/apt  Entire home/apt
2     Private room     Private room
3  Entire home/apt  Entire home/apt
4  Entire home/apt  Entire home/apt

You will get a dataframe with two columns "0" and "1", let's made them more understandable by renaming the column names into 'prey' and 'y'.

In [28]:
testdf.columns=('prey','y')

### <a id="Classification Accuracy">Classification Accuracy</a>

In [30]:
# check the accuracy in predicting the right room type
# compare predicted y value and the real y value
testdf['diff']=np.where(testdf.prey==testdf.y,1,0)
# calculate the proportion of matched pairs
print('% correct =',sum(testdf['diff'])/len(testdf['diff'])*100)

% correct = 62.69012930573861


As we had the predicting accuracy at 62.55%, we will further build out the [log loss function](http://wiki.fast.ai/index.php/Log_Loss) to see how much error in the predictions.

In [31]:
PredProb=neigh.predict_proba(X_test)
pred=np.asmatrix(PredProb)
pred.shape

(28073, 4)

In [33]:
pred.columns=('Entire home/apt','Private room','Shared room')
s=np.asmatrix(pd.get_dummies(y_test))
def f(x):
    return sp.log(sp.maximum(sp.minimum(x,1-10**-5),10**-5))
f=np.vectorize(f)
predf=f(pred)
mult=np.multiply(predf,s)
print('log loss =',np.sum(mult)/-len(y_test))

log loss = 0.8909946419842455


This log loss is quite high so let's see if we can improve this by increasing our k value. Since, it would be annoying to change the value and run it, I figure it'll be faster to run a for loop through values of $k$ from odd numbers between 3 to 39 (represented by $j$). I also wanted to have at least 5 samples in each $k$ to give us a good average (represented by $i$).

In [34]:
accbig=[]
loglossbig=[]

def f(x):
    return sp.log(sp.maximum(sp.minimum(x,1-10**-5),10**-5))
f=np.vectorize(f)

for j in range(3,40,2):
    logloss=[]
    acc=[]
    for i in range(5):
        #split data
        X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, random_state=i)
        neigh = KNeighborsClassifier(n_neighbors=j)
        #train classifier
        neigh.fit(X_train, y_train)
        
        #find % predicted correctly for this k
        predVal=neigh.predict(X_test)
        mat=[predVal,y_test]
        testdf=pd.DataFrame(mat).transpose()
        testdf.columns=('prey','y')
        testdf['diff']=np.where(testdf.prey==testdf.y,1,0)
        acc.append(sum(testdf['diff'])/len(testdf['diff']))
        
        #find the logloss for this k
        PredProb=neigh.predict_proba(X_test)
        pred=np.asmatrix(PredProb)
        pred.columns=('Entire home/apt','Private room','Shared room')
        s=np.asmatrix(pd.get_dummies(y_test))
        predf=f(pred)
        mult=np.multiply(predf,s)
        logloss.append(np.sum(mult)/-len(y_test))
    loglossbig.append(np.mean(logloss))
    accbig.append(np.mean(acc))
print(accbig)
print(loglossbig)

[0.6058917821394222, 0.6156876714280626, 0.6209240195205357, 0.6250489794464432, 0.6277989527303814, 0.6298080005699427, 0.6302639546895593, 0.6309550101521034, 0.6304634346168917, 0.6305489260143198, 0.6309122644533893, 0.6317885512770278, 0.6321305168667403, 0.6316888113133616, 0.6317244327289566, 0.6317814269939087, 0.6319025398069319, 0.6317101841627186, 0.6322160082641683]
[1.9412841250453616, 1.2516850623276903, 1.008894494506966, 0.9022951337651893, 0.8481945355840264, 0.8136561028022786, 0.7937198213327327, 0.7784912168210506, 0.7685315341169079, 0.761810786289848, 0.7577235309714843, 0.753378901075975, 0.7504233811697629, 0.7473502302692525, 0.745064669606088, 0.7427882947446133, 0.7410367902690358, 0.7395735430596284, 0.7387624071479071]


In [35]:
# plot this against every K to see the decrease
plt.plot(range(3,40,2),loglossbig)
plt.ylabel('logloss')
plt.xlabel('k value')
plt.title('KNN logloss on longitude and latitude')

In [36]:
plt.plot(range(3,40,2),accbig)
plt.ylabel('% predicted correctly')
plt.xlabel('k value')
plt.title('KNN prediction on longitude and latitude')

Even though the performance for this isn't amazing, we can see that there are some predictive value that we can use from longtitude and latitude data. We could further check the accuracy of predication at specific $k$ value. For example, 

In [ ]:
from sklearn.metrics import accuracy_score

# instantiate learning model (k = 25) 
knn = KNeighborsClassifier(n_neighbors=25)
# fitting the model
knn.fit(X_train, y_train)
# predict the response
pred = knn.predict(X_test)
# evaluate accuracy
print (accuracy_score(y_test, pred))

### <a id='Task 9'>Task 9</a> (Optional)

Price distribution for Airbnb in London (purely statistics), 3 missions to complete.
1. Airbnb price distribution in London from west to east. 

   **Hint**: Scatter plotted the price against longitude calling `seaborn`.

In [37]:
traindf.columns.values

array(['id', 'listing_url', 'scrape_id', 'last_scraped', 'name',
       'summary', 'space', 'description', 'experiences_offered',
       'neighborhood_overview', 'notes', 'transit', 'access',
       'interaction', 'house_rules', 'thumbnail_url', 'medium_url',
       'picture_url', 'xl_picture_url', 'host_id', 'host_url',
       'host_name', 'host_since', 'host_location', 'host_about',
       'host_response_time', 'host_response_rate', 'host_acceptance_rate',
       'host_is_superhost', 'host_thumbnail_url', 'host_picture_url',
       'host_neighbourhood', 'host_listings_count',
       'host_total_listings_count', 'host_verifications',
       'host_has_profile_pic', 'host_identity_verified', 'street',
       'neighbourhood', 'neighbourhood_cleansed',
       'neighbourhood_group_cleansed', 'city', 'state', 'zipcode',
       'market', 'smart_location', 'country_code', 'country', 'latitude',
       'longitude', 'is_location_exact', 'property_type', 'room_type',
       'accommodates', 'bath

In [45]:
traindf['price'] = traindf.apply(lambda row: row['price'].replace('$','').replace(',',''), axis = 1)
traindf['price'] = traindf['price'].astype(float)

In [46]:
# your code here
sns.scatterplot(traindf.longitude, traindf.price)

Can you try to interpret the distribution in a geographcial language then? Your answers below:

**---------------------------------------------------------**

2. Airbnb price distribution in London from south to north.

   **Hint:** Scatter plotted the price against latitude calling `seaborn`.


In [47]:
# your code here
sns.scatterplot(traindf.latitude, traindf.price)

Can you try to interpret the distribution in a geographcial language then? Your answers below:

**---------------------------------------------------------**

3. The average price and price range for each room type.
   **Hint:** Price statistics by room type, using `groupby`.

In [48]:
traindf.groupby('room_type')['price'].describe().reset_index()

room_type    count        mean         std   min    25%    50%  \
0  Entire home/apt  47445.0  169.910676  248.694342   0.0  90.00  120.0   
1       Hotel room   1113.0  232.607367  572.020738  14.0  80.00  148.0   
2     Private room  35882.0   57.219023  125.231725   0.0  33.00   45.0   
3      Shared room    628.0   53.355096  115.340546   0.0  19.75   28.0   

     75%      max  
0  180.0  12345.0  
1  200.0   9999.0  
2   60.0   7852.0  
3   50.0   2000.0

Can you try to interpret the Output? Your answers below:

**---------------------------------------------------------**

OK, some unbelievable prices pop up, and we want to get rid of these outliers for further analysis. So let's firstly get a general idea of the spatial distribution among defined price ranges, say, below £100, £100-£200, £200-£400, £400-£600 and above £600, and call `Bokeh` to plot again. 

In [50]:
# define your points' coordinates for each price range
Lat100=traindf['latitude'][traindf['price']<100]
Long100=traindf['longitude'][traindf['price']<100]
Lat200=traindf['latitude'][(traindf['price']<200)&(traindf['price']>=100)]
Long200=traindf['longitude'][(traindf['price']<200)&(traindf['price']>=100)]
Lat400=traindf['latitude'][(traindf['price']<400)&(traindf['price']>=200)]
Long400=traindf['longitude'][(traindf['price']<400)&(traindf['price']>=200)]
Lat600=traindf['latitude'][(traindf['price']<600)&(traindf['price']>=400)]
Long600=traindf['longitude'][(traindf['price']<600)&(traindf['price']>=400)]
Latup=traindf['latitude'][(traindf['price']>=600)]
Longup=traindf['longitude'][(traindf['price']>=600)]

In [51]:
p = figure(title="Airbnb prices",y_range=(51.28,51.7),x_range=(-0.6,0.4))
p.xaxis.axis_label = 'latitude'
p.yaxis.axis_label = 'longitude'

# plot points in each price range with different colors
p.circle(Long100,Lat100,size=3,color=rainbow.as_hex()[0],fill_alpha=0.6,line_alpha=0.6,legend_label='<£100')
p.circle(Long200,Lat200,size=3,color=rainbow.as_hex()[1],fill_alpha=0.6,line_alpha=0.6,legend_label='£200')
p.circle(Long400,Lat400,size=3,color=rainbow.as_hex()[4],fill_alpha=0.6,line_alpha=0.6,legend_label='£400')
p.circle(Long600,Lat600,size=3,color=rainbow.as_hex()[5],fill_alpha=0.6,line_alpha=0.6,legend_label='£600')
p.circle(Latup,Longup,size=3,color=rainbow.as_hex()[3],fill_alpha=0.9,line_alpha=1,legend_label='up')
p.legend.location = 'top_right'
show(p, notebook_handle=True)

I intentially highlighted the points with price above £600 by higher definition of its point transparency, however, we still can't spotted too much in that category. It indicates that majority of the renting prices are below £600 roughly.

## <a id="Kernel Density Estimation (KDE)">Kernel Density Estimation (KDE)</a> 

A density plot is a smoothed, continuous description of the data distribution, and [kernel density estimation](https://en.wikipedia.org/wiki/Kernel_density_estimation) could be the most typical density plot receiving wide popularity. It draws a continuous curve (the kernel) at each data point and adds all of these curves together to make a smooth density estimation. 

The most often used kernel is a Gaussian, within which the kernel is mathmetically a positive function for `k` and `h`:
<img  height="100" src="kernel function.png">

where `h` as the bandwidth parameter, controlling the tradeoff between bias and variance in the result. Larger bandwidth leads to smoother (i.e. high-bias) density distribution, while smaller bandwidth leads to an unsmooth (i.e. high-variance) density distribution, and finally produces a Gaussian bell curve at each data point. More detailed explaination could be explored from [Kernel Density Estimation](https://scikit-learn.org/stable/modules/density.html#kernel-density-estimation). 

Besides of the common Gaussian Kernel, there are also other 5 kernel forms used in sklearn:
<img  height="100" src="kernel formats .png">

The most common use of KDE is in graphically representing distributions of points. There are many ways to visualize the results of Kernal Density Estimates, e.g. the `seaborn` plot we used last semester and in this practical. In the `seaborn` visualization library, KDE is built in and automatically used to help visualize points in one and two dimensions.

### <a id="Univariate Distribution in 1D">Univariate Distribution in 1D</a>

In [52]:
sns.set(color_codes=True)
kdeprice=traindf.price[traindf['price']<600]
# call KDE function in seaborn
sns.kdeplot(kdeprice, shade=True)

If you check the parameters for [seaborn.kdeplot](https://seaborn.pydata.org/generated/seaborn.kdeplot.html), you will find the "bw" (bandwidth) parameter controlling how tightly the estimation is fit to the data, similar to the bin size in a histogram. As corresponding to the width of the kernels we plotted above, we may try larger or smaller values instead, to compare with the default behavior.

In [53]:
sns.kdeplot(kdeprice)
sns.kdeplot(kdeprice, bw=.2, label='bw: 0.2')
sns.kdeplot(kdeprice, bw=2, label='bw: 2')
plt.legend()

So far for this Airbnb price data, it seems that bandwidth at 2 is much better than that bw at 0.2. The nature of the Gaussian KDE process means that estimation extends past the extreme (largest and smallest) values in the dataset; so we can control where we want to "start" or "stop" the past by defining the "cut" parameter. 

In [54]:
sns.kdeplot(kdeprice, shade=True, cut=0)
sns.rugplot(kdeprice)

The plot cut at "0" as defined, however, you may also spotted that only the drawn curve is affected, but the fit line doesn't change at all.

### <a id="Bivariate Distribution in 2D">Bivariate Distribution in 2D</a> 

In [55]:
sns.jointplot(x='longitude', y='latitude', data=traindf, kind="kde")

You can also draw a two-dimensional kernel density plot with the `kdeplot` function. This allows you to draw this kind of plot onto a specific (and possibly already existing) matplotlib axes, whereas the `jointplot` function manages its own figure:

In [56]:
f, ax = plt.subplots(figsize=(6, 6))
sns.kdeplot(traindf.longitude, traindf.latitude, ax=ax)
sns.rugplot(traindf.longitude, color="g", ax=ax)
sns.rugplot(traindf.latitude, vertical=True, ax=ax)

If you wish to show the bivariate density more continuously, you can simply increase the number of contour levels:

In [57]:
f, ax = plt.subplots(figsize=(6, 6))
cmap = sns.cubehelix_palette(as_cmap=True, dark=0, light=1, reverse=True)
sns.kdeplot(traindf.longitude, traindf.latitude, cmap=cmap, n_levels=60, shade=True)

The `jointplot` function uses a JointGrid to manage the figure. For more flexibility, you may want to draw your figure by using JointGrid directly. `jointplot` returns the JointGrid object after plotting, which you can use to add more layers or to tweak other aspects of the visualization:

In [59]:
g = sns.jointplot(x='longitude', y='latitude', data=traindf, kind="kde", color="m")
g.plot_joint(plt.scatter, c="w", s=30, linewidth=1, marker="+")
g.ax_joint.collections[0].set_alpha(0)
g.set_axis_labels("$longitude$", "$latitude$")

### <a id="Task 10">Task 10</a> 
Plot bivariate distribution between Airbnb price and corresponding distance to City Center.
1. Calculate the distances between airbnb and city center, which is Charing Cross at (51.5081, -0.1248).
2. Apply what we've covered before to plot your own bivariate distribution.

In [58]:
import math
# define the coordinates of each point
x1 = traindf['latitude']
y1 = traindf['longitude']

# an empty list for distance
distance=[]
# loop to calculate the distance between each point and city center
for i in range(len(x1)):
    xa, ya=x1[i], y1[i]
    distance.append((((xa-51.5081)**2)+((ya-(-0.1248))**2))**(1/2))
# list the distance results
print(distance)

4349145925571, 0.10032014403897507, 0.20348400158243393, 0.05858432042790965, 0.09147217828389033, 0.0626806780435568, 0.1927849208314801, 0.09997051615350981, 0.10212478347590372, 0.13651579432432212, 0.08182576916839546, 0.2008411265154619, 0.04240928436085466, 0.16337327351803949, 0.08743850925078778, 0.08405113205662319, 0.061683430514199146, 0.019681895233943612, 0.15694837654464544, 0.13020454869166428, 0.041480594258034756, 0.10130445449238638, 0.20982708690729138, 0.014456987929720297, 0.04455915843011675, 0.045762003889691004, 0.10971379220499178, 0.07868913584479088, 0.1091420991185348, 0.05835918608068482, 0.052793402996967616, 0.0402862011115465, 0.04578080383741065, 0.19036071023191747, 0.025722647608674466, 0.0548799599125213, 0.0035320956951954497, 0.02872881654367298, 0.10156421269325006, 0.2139815753750773, 0.19889150107533532, 0.13162387777299425, 0.026669797524544167, 0.08903818113595989, 0.08618647341665651, 0.055651948752941764, 0.03503774108015489, 0.0694402916180

In [61]:
g = sns.jointplot(x=distance, y=traindf['price'], data=traindf, kind="kde", color="m")
g.plot_joint(plt.scatter, c="r", s=50, linewidth=1, marker="+")
g.ax_joint.collections[0].set_alpha(0)
g.set_axis_labels("$distance$", "$price$")

Can you try to interpret the result below?

`________________________________________________________________________________________________`


### <a id="Multivariate KDE">Multivariate KDE<a/> 
Now we will look at a slightly more sophisticated use of KDE's visualization for the distribution of 4 different  airbnb room types in London distributions. 

In [62]:
# load the AirBnB data into a GeoDataFrame called `sdf` (spatial sample dataframe)
import os
import shapely
from shapely.geometry import Point
geometry = [Point(xy) for xy in zip(traindf.longitude, traindf.latitude)]
crs      = {'init': 'epsg:4326'} # What projection is lat/long?
sdf      = gpd.GeoDataFrame(traindf, crs=crs, geometry=geometry)
sdf      = sdf.to_crs({'init': 'epsg:27700'}) # Reproject into OSGB

# Check the output
sdf.head(3)

id                         listing_url       scrape_id last_scraped  \
0  11551  https://www.airbnb.com/rooms/11551  20191105115249   2019-11-06   
1  38151  https://www.airbnb.com/rooms/38151  20191105115249   2019-11-06   
2  13913  https://www.airbnb.com/rooms/13913  20191105115249   2019-11-06   

                                         name  \
0  Arty and Bright London Apartment in Zone 2   
1                         Double room/ lounge   
2         Holiday London DB Room Let-on going   

                                             summary  \
0  Unlike most rental apartments out there my fla...   
1                                                NaN   
2  My bright double bedroom with a large window h...   

                                               space  \
0  Amenities Bedding: 1 Double bed, 1 living room...   
1  Comfortable, large double room /lounge area av...   
2  Hello Everyone, I'm offering my lovely double ...   

                                         description experiences_offered  \
0  Unlike most rental apartments out there my fla...              family   
1  Comfortable, large double room /lounge area av...                none   
2  My bright double bedroom with a large window h...            business   

                               neighborhood_overview  ...  \
0  Not even 10 minutes by metro from Victoria Sta...  ...   
1                                                NaN  ...   
2  Finsbury Park is a friendly melting pot commun...  ...   

  is_business_travel_ready          cancellation_policy  \
0                        f  strict_14_with_grace_period   
1                        f                     flexible   
2                        f                     moderate   

  require_guest_profile_picture require_guest_phone_verification  \
0                             f                                t   
1                             f                                f   
2                             f                                f   

  calculated_host_listings_count  calculated_host_listings_count_entire_homes  \
0                              2                                            2   
1                              1                                            0   
2                              2                                            1   

   calculated_host_listings_count_private_rooms  \
0                                             0   
1                                             1   
2                                             1   

  calculated_host_listings_count_shared_rooms  reviews_per_month  \
0                                           0               1.58   
1                                           0                NaN   
2                                           0               0.17   

                        geometry  
0  POINT (530885.122 175377.940)  
1  POINT (533100.397 170667.128)  
2  POINT (531005.968 187150.843)  

[3 rows x 107 columns]

In [63]:
## airbnb listing data read csv file 4 types of airbnb
sdf_group = sdf.groupby('room_type').size().reset_index(name='count')
sdf_sort = sdf_group.sort_values(['count'], ascending=False).reset_index(drop=True)
sdf_sort

room_type  count
0  Entire home/apt  47445
1     Private room  35882
2       Hotel room   1113
3      Shared room    628

In [64]:
in_type=sdf_sort['room_type']

In [65]:
sdf['longitude'].notnull().count() # check whether they all have longitude data
sdf['latitude'].notnull().count() # check whether they all have latitude data

85068

In [66]:
# calculate the mean value of coordinates for each room type
sdf_group = sdf.groupby('room_type')
loc_sdf_group = sdf_group[['latitude', 'longitude']].mean()
x = loc_sdf_group.longitude.values
y = loc_sdf_group.latitude.values
loc_sdf_group.head()

latitude  longitude
room_type                            
Entire home/apt  51.509764  -0.134267
Hotel room       51.505819  -0.140663
Private room     51.509907  -0.120385
Shared room      51.513230  -0.113692

In [68]:
import matplotlib.pyplot as plt
import seaborn as sns

# Set up the plotting base
new_gdb = gpd.GeoSeries(sdf[['longitude', 'latitude']].apply(Point, axis=1), crs="+init=epsg:4326")
bbox = new_gdb.total_bounds
titles=["Kernel Density: "+in_type[i] for i in range(4)]
fig, ax = plt.subplots(2,2,figsize=(15,6))
fig.tight_layout(pad = 0.4, w_pad = 4.0, h_pad = 4.0)

# sets the x and y limits for each function 
# otherwise the density maps will be very small
ax0 = plt.subplot2grid((8,8), (0,0),rowspan=3, colspan=3) 
ax0.set_title(titles[0], fontsize =16)
ax0.set_xlim(bbox[0], bbox[2])
ax0.set_ylim(bbox[1], bbox[3]) 

ax1 = plt.subplot2grid((8,8), (4,0),rowspan=3, colspan=3)
ax1.set_title(titles[1], fontsize =16)
ax1.set_xlim(bbox[0], bbox[2])
ax1.set_ylim(bbox[1], bbox[3]) 

ax2 = plt.subplot2grid((8,8), (0,4),rowspan=3, colspan=3)
ax2.set_title(titles[2], fontsize =16)
ax2.set_xlim(bbox[0], bbox[2])
ax2.set_ylim(bbox[1], bbox[3]) 

ax3 = plt.subplot2grid((8,8), (4,4),rowspan=3, colspan=3)
ax3.set_title(titles[3], fontsize =16)
ax3.set_xlim(bbox[0], bbox[2])
ax3.set_ylim(bbox[1], bbox[3]) 

gdfnew0 = sdf[sdf['room_type']==in_type[0]]
sns.kdeplot(gdfnew0.longitude, gdfnew0.latitude, shade = True, cmap = 'Reds', ax=ax0) 
gdfnew1 = sdf[sdf['room_type']==in_type[1]]
sns.kdeplot(gdfnew1.longitude, gdfnew1.latitude, shade = True, cmap = 'Blues', ax=ax1)
gdfnew2 = sdf[sdf['room_type']==in_type[2]]
sns.kdeplot(gdfnew2.longitude, gdfnew2.latitude, shade = True, cmap = 'Greens', ax=ax2)
gdfnew3 = sdf[sdf['room_type']==in_type[3]]
sns.kdeplot(gdfnew3.longitude, gdfnew3.latitude, shade = True, cmap = 'Purples', ax=ax3)

sns.set(style = 'whitegrid') # aesthetics
sns.despine(left=True) # aesthetics
sns.set_context('paper') # aesthetics
plt.axis('equal')
plt.show() 

# Credits!

### (Optional) <a id="Others channels to understand KDE">Others channels to understand KDE</a> 

Just as stated in previous practicals, there are always multiple ways to reach at your goals and get problems solved; so does KDE. Upon your understanding of the statistical rationale of KDE, you may find other methods to fulfill your requests, for example: 
1. `gaussian_kde` in `SciPy`: contains only the common Gaussian Kernel; 
2. `KernelDensity` in `Scikit-learn`: contains six kernels, each of which can be used with one of about a dozen distance metrics, resulting in a very flexible range of effective kernel shapes; 
3. `KDEUnivariate` & `KDEMultivariate` in Statsmodels: contains seven kernels.

We will make use of the aforementioned methods in order for our airbnb data, to get you more understanding of the parameters of KDE: **kernel**, which specifies the shape of the distribution placed at each point; and **bandwidth**, which controls the size of the kernel at each point.

### Univariate KDE in 1D
We will keep using the London Airbnb price data, which are less than £600, as defined in previous section as $kdeprice$, to demonstrate the principles of Kernel Density Estimation in one dimension. Firstly, let's get a rough idea of the data by creating histogram simply with the `plt.hist()` function, and with the density parameter specification to get the height of the bins reflecting probability density. 

In [69]:
X=np.array(kdeprice)
mean=np.mean(X)
var=np.var(X)
std=np.sqrt(var)
X_plot = np.linspace(min(X),max(X), 1000) # set up a sample size at 1000
print(mean,var,std)

106.1364129851227 7458.1372988693265 86.36050775018246


You can read the mean value for price from the output and use it as benchmark for this section:

In [70]:
# Compute histogram of Samples
n, bins,patches=plt.hist(X,bins=100,density=True,facecolor='g',edgecolor='red', alpha=0.8)
# try to change the value of bins, figure out the variations
plt.axvline(label='Mean=£106',x=106,linestyle='dashed')
plt.axvline(label='Mean-2sigma=-£67',x=-67,linestyle='dashed')
plt.axvline(label='Mean+2sigma=£279',x=279, linestyle='dashed')
plt.xlabel('Prices(£)')
plt.ylabel('Probability')
plt.title('Histogram of Airbnb prices distribution')

In [71]:
from scipy.stats import norm
X = np.array(kdeprice) # load the data
count = sum(norm(Xi).pdf(X_plot) for Xi in X)  # pdf stands for probability distribution function

plt.fill_between(X_plot, count, alpha=0.75)
plt.plot(X, np.full_like(X, -0.1), '|k', markeredgewidth=1)
plt.axis([-20, 620, 0, 800]) # set the axis limits

In [72]:
# Note that scipy weights its bandwidth by the covariance of the input data.
# To make the results comparable to the other methods, we use the bandwidth at 0.2
from scipy.stats import gaussian_kde
kde_scipy = gaussian_kde(X, bw_method=0.2)
log_dens_scipy = kde_scipy.evaluate(X_plot)

plt.fill_between(X_plot, log_dens_scipy, alpha=0.5)
plt.plot(X, np.full_like(X, -0.1), '|k', markeredgewidth=1)
plt.ylim(-0.001, 0.014)

In [73]:
from scipy.stats import kurtosis, skew
print("Excess kurtosis of normal distribution ( should be 0):{}".format(kurtosis(X)))
print("Skewness of normal distribution ( should be 0):{}".format(skew(X)))

Excess kurtosis of normal distribution ( should be 0):5.5485160038397385
Skewness of normal distribution ( should be 0):2.089678435279571


Now let's turn from `Scipy` to `Scikit-learn`.

In [74]:
from sklearn.neighbors.kde import KernelDensity
# instantiate and fit the Gaussian KDE model
kde_sklearn = KernelDensity(kernel='gaussian', bandwidth=0.2).fit(X[:,None])
# score_samples returns the log of the probability density
log_dens_sklearn = kde_sklearn.score_samples(X_plot[:, None])

plt.fill_between(X_plot, np.exp(log_dens_sklearn), alpha=0.75)
plt.plot(X, np.full_like(X, -0.1), '|k', markeredgewidth=1)
plt.ylim(-0.001, 0.014)

How about the 3rd method in `statsmodels`?

In [75]:
from statsmodels.nonparametric.kde import KDEUnivariate
X_new=X.astype(np.double)  # Try to explain do we need this code? what will happen if you still use variable X?
kde_statsmu = KDEUnivariate(X_new)
kde_statsmu.fit() # Estimate the densities

fig = plt.figure(figsize=(6,4))
ax = fig.add_subplot(111)
ax.hist(X_new, bins=100, normed=True, color='red')
ax.plot(kde_statsmu.support, kde_statsmu.density, lw=-2, color='black')

In [76]:
fig = plt.figure(figsize=(6,4))
ax = fig.add_subplot(111)
# Plot the histrogram
ax.hist(X_new, bins=20, normed=True, label='Histogram from samples', 
        zorder=5, edgecolor='k', alpha=0.5)
# Plot the KDE as fitted using the default arguments
ax.plot(kde_statsmu.support, kde_statsmu.density, lw=3, label='KDE from samples', zorder=10)
ax.legend(loc='best')

In [77]:
fig = plt.figure(figsize=(6,4))
ax = fig.add_subplot(111)
# Plot the true distribution
true_values = (norm.pdf(loc=-1, scale=0.5, x=kde_statsmu.support)*0.25
              + norm.pdf(loc=1, scale=0.5, x=kde_statsmu.support)*0.75)

# different defination of location, scale and weights for 2 normal distribution dataset
ax.plot(kde_statsmu.support, true_values, lw=3, label='True distribution', zorder=15)

# Plot the samples
ax.scatter(X_new, np.abs(np.random.randn(X_new.size))/40, 
           marker='o', color='k', zorder=20, label='Samples', alpha=0.5)
ax.legend(loc='best')
ax.grid(True, zorder=5)

The bandwidth of the kernel can be adjusted using the bw argument. In the following example, a bandwidth of bw=0.2 seems to fit the data well.

In [78]:
fig = plt.figure(figsize=(12, 5))
ax = fig.add_subplot(111)

# Plot the histrogram
ax.hist(X_new, bins=25, label='Histogram from samples', 
        zorder=5, edgecolor='k', normed=True, alpha=0.5)

# Plot the KDE for various bandwidths
for bandwidth in [0.1, 0.2, 0.4]:
    kde_statsmu.fit(bw=bandwidth) # Estimate the densities
    ax.plot(kde_statsmu.support, kde_statsmu.density, '--', lw=2, color='k', zorder=10,
            label='KDE from samples, bw = {}'.format(round(bandwidth, 2)))

# Plot the true distribution
ax.plot(kde_statsmu.support, true_values, lw=3, label='True distribution', zorder=15)

# Plot the samples
ax.scatter(X_new, np.abs(np.random.randn(X_new.size))/50, 
           marker='o', color='red', zorder=5, label='Data samples', alpha=0.5)

ax.legend(loc='best')
ax.set_xlim([0, 600])
ax.grid(True, zorder=5)

## Credits!

## Take home work -- GIS realization (Optional)

**Task**: Nearest Neighbour Distances analysis

For ArcGIS user, hints:
- in ArcMap, activate the Spatial Analyst extension (i.e. check that the checkbox next to the Spatial Analysis extension is checked in the “Extension” menu);
- in ArcToolBox, open Spatial Statistics Tools > Analyzing Patterns > Average Nearest Neighbor to carry out NN analysis.
- a report will be produced to explain the distribution of the nearest neighbor distances.

For QGIS user, hints:
- Load the London Pub data (CRS: WGS 84, Authority ID: EPSG:4326). 
- Select from the main menu, Vector -> Analysis Tools -> Distance Matrix….

#### Contributors:
The following individual(s) have contributed to these teaching materials: Yijing Li (yijing.li@kcl.ac.uk).

#### License
These teaching materials are licensed under a mix of [The MIT License](https://opensource.org/licenses/mit-license.php) and the [Creative Commons Attribution-NonCommercial-ShareAlike 4.0 license](https://creativecommons.org/licenses/by-nc-sa/4.0/).


